In [15]:
#前処理後のindex作るための処理
import os
import elasticsearch as es
import math
import numpy as np
from itertools import chain
import sys
import tensorflow as tf
import matplotlib.pyplot as plt

ES_HOST = "localhost"
escon = es.Elasticsearch(ES_HOST, port=9200)
GACRP_HOME=os.environ['GACRP_HOME']

# ESのデータ量依存設定値のグローバル変数化
# scrollのタイムアウト時間
es_s_time='2m'

maxPartition=90


In [16]:
indataStartYmd=20160801
indataEndYmd=20161031
forecastStartYmd=20161101
forecastEndYmd=20161231

In [17]:
# 元データ取得

def getInputData(startymd,endymd):
    es_size=10000
    body = {
      "_source": [
        "fullVisitorId","date",
        "channelGrouping","visitNumber","isMobile","country","hits","bounces",
        "newVisits","source","medium","isTrueDirect","transactionRevenue"
      ],
      "query": {
        "bool": {
          "must": [
            {
              "range": {
                "date": {
                  "gt": startymd,
                  "lt": endymd
                }
              }
            }
          ],
          "must_not": [],
          "should": []
        }
      },
      "from": 0,
      "size": 0,
      "sort": [],
      "aggs": {}
    }
  
    res=escon.search(index='gacrp_index',body=body,scroll=es_s_time,size=es_size)
    es_s_id=res['_scroll_id']
    es_s_size=len(res["hits"]["hits"])
    
    return(res,es_s_id,es_s_size)


In [18]:
#fullVisitorIdごとに、指定した期間のrevenueを取得
def getRevenue(startYmd,endYmd,partitionNumber,maxPartition):
    es_size=10000
    body = {
        "size":0,
        "aggs":{
            "agg_fullVisitorId":{
                "terms":{
                    "field":"fullVisitorId.keyword",
                    "include":{
                        "partition":partitionNumber,
                        "num_partitions":maxPartition
                    },
                    "size":10000
                },
                "aggs":{
                    "agg_revenue":{
                        "sum":{"field":"transactionRevenue"}
                    }
                }
            }
        },
        "query":{
            "bool":{
                "must":[
                    {"range": {"date": {
                                "gt": startYmd,"lt": endYmd
                    }}}
                ]
            }
        }
    }
    #print(body)
    res=escon.search(index='gacrp_index',body=body)
    #revenue=math.log(int(res['aggregations']['agg_revenue']['value'])+1)
    #print(revenue)
    return(res['aggregations']['agg_fullVisitorId']['buckets'])


In [19]:
#oneHotベクトル化
def es2oneHot(res,data):
    for i in range(len(res["hits"]["hits"])):
        row=res["hits"]["hits"][i]["_source"]
        rec=[]

        col_date=row['date']
        col_fullVisitorId=row['fullVisitorId']
        
        if row['channelGrouping']=='Display':
            col_channelGrouping=1
        elif row['channelGrouping']=='Social':
            col_channelGrouping=2
        else:
            col_channelGrouping=0
        oneHot_col_channelGrouping=np.eye(2+1)[col_channelGrouping]
        
        #visitNumberは最大を5で打ち切って0～1にnormalize。
        col_visitNumber=min(int(row['visitNumber']),5)/5.0 

        if row['isMobile']=="TRUE":
            col_isMobile=1
        else:
            col_isMobile=0

        if row['country']=="United States":
            col_country =1
        elif row['country']=="Canada":
            col_country =2
        elif row['country']=="Japan":
            col_country=3
        else:
            col_country=0
        oneHot_col_country=np.eye(3+1)[col_country]
    
        col_hits=math.log10(int(row['hits'])*1.0)
    
        if row['bounces']=="1":
            col_bounces=1
        else:
            col_bounces=0

        if row['newVisits']== "1":
            col_newVisits=1
        else:
            col_newVisits=0
    
        if row['source']=="mail.googleplex.com" or row['source']=="dfa":
            col_source =1
        elif row['source']=="(direct)":
            col_source=2
        else:
            col_source=0
        oneHot_col_source=np.eye(2+1)[col_source]
        
        if row['medium']=="cpm":
            col_medium=1
        else:
            col_medium=0
        oneHot_col_medium=np.eye(1+1)[col_medium]
    
        if row['isTrueDirect']=="1":
            col_isTrueDirect=1
        else:
            col_isTrueDirect=0
    
        #revenue = math.log(int(row['transactionRevenue'])+1)
    
        l=[oneHot_col_channelGrouping,[col_visitNumber],[col_isMobile],oneHot_col_country,[col_hits],[col_bounces],[col_newVisits],oneHot_col_source,oneHot_col_medium,[col_isTrueDirect]]
        data.append([col_fullVisitorId,list(chain.from_iterable(l))])
        #data.append([col_fullVisitorId,l])
        #ans.append(revenue)
    
    return(data)

In [20]:
rowdata=[]
ans = []

res,es_s_id,es_s_size=getInputData(indataStartYmd,indataEndYmd)
while(es_s_size>0):
    rowdata=es2oneHot(res,rowdata)
    res=escon.scroll(scroll_id=es_s_id,scroll=es_s_time)
    es_s_id=res['_scroll_id']
    es_s_size=len(res["hits"]["hits"])

    print(len(rowdata))

10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000
130000
140000
150000
160000
170000
180000
190000
200000
210000
220000
230000
237728


In [71]:
#rowdataを対象期間のfullVisitorIdごとに集約して予測期間のtransactionRevenueを当てる
rowdata=sorted(rowdata,key=lambda x:x[0])
print("ソート完了")
key_fullVisitorId=rowdata[0][0]
sumdata=[]

#print(rowdata[0][1])
#print(key_fullVisitorId)

tmp_indata=[]
tmp_indata.append(rowdata[0][1])
tmp_cnt=1
for i in range(1,len(rowdata)):
    #if i %10000==0:
    #    print("集約処理実行中："+str(i) )
    if key_fullVisitorId==rowdata[i][0]:
        tmp_indata.append(rowdata[i][1])
        tmp_cnt+=1
    else:
        #列方向に平均をとってappend
        #print(tmp_indata)
        if tmp_cnt==1:
            sumdata.append([key_fullVisitorId,tmp_indata])
        else:            
            sumdata.append([key_fullVisitorId,np.average(tmp_indata,axis=1)])
        #ans.append(getRevenueByFullVisitorId(key_fullVisitorId,forecastStartYmd,forecastEndYmd))
        key_fullVisitorId=rowdata[i][0]
        tmp_indata=[]
        tmp_indata.append(rowdata[i][1])
        tmp_cnt=1
if tmp_cnt==1:
    sumdata.append([key_fullVisitorId,tmp_indata])
else:
    sumdata.append([key_fullVisitorId,np.average(tmp_indata,axis=1)])

#ans.append(getRevenueByFullVisitorId(key_fullVisitorId,forecastStartYmd,forecastEndYmd))    

print(len(sumdata))

ソート完了
[[1.0, 0.0, 0.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.8, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.6, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.47712125471966244, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.8, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 1.0, 0, 1.0, 0.0, 0.0, 0.0, 0.47712125471966244, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.3010299956639812, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.6, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 0.7781512503836436, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.7781512503836436, 0, 1, 1.0, 0.0, 0.0, 1.0,

[[0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.9030899869919435, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 1.0, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 1.0, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.9030899869919435, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.8450980400142568, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.6, 0, 0.0, 1.0, 0.0, 0.0, 1.0, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 1.0, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.9030899869919435, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.8, 0, 0.0, 1.0, 0.0, 0.0, 1.0, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0

[[0.0, 0.0, 1.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.6, 0, 0.0, 0.0, 0.0, 1.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.2, 0, 0.0, 0.0, 0.0, 1.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.4, 0, 0.0, 0.0, 0.0, 1.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 1, 0.0, 1.0, 0.0, 0.0, 0.6020599913279624, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 1, 0.0, 1.0, 0.0, 0.0, 0.47712125471966244, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.9542425094393249, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 1.6334684555795866, 

[[0.0, 0.0, 1.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 1, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 1, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 1, 0.0, 0.0, 1.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.6, 0, 1.0, 0.0, 0.0, 0.0, 0.7781512503836436, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.4, 0, 1.0, 0.0, 0.0, 0

[[1.0, 0.0, 0.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.6, 0, 0.0, 1.0, 0.0, 0.0, 1.9637878273455553, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 0.47712125471966244, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.8, 0, 0.0, 1.0, 0.0, 0.0, 1.4471580313422192, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 1.0, 1, 0.0, 1.0, 0.0, 0.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 1, 0.0, 1.0, 0.0, 0.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 1, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 1, 0.0, 1.0, 0.0, 0.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.47712125471966244, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.477

...

[[1.0, 0.0, 0.0, 0.4, 1, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 1, 0.0, 1.0, 0.0, 0.0, 1.5314789170422551, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 1, 1.0, 0.0, 0.0, 0.0, 0.3010299956639812, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.6, 1, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 1, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.4, 1, 1.0, 0.0, 0.0, 0.0, 0.7781512503836436, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 1, 1.0, 0.0, 0.0, 0.0, 0.7781512503836436, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 0.6020599913279624, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 1.1760912590556813, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 

[[1.0, 0.0, 0.0, 0.2, 1, 0.0, 1.0, 0.0, 0.0, 0.7781512503836436, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 1, 0.0, 1.0, 0.0, 0.0, 0.8450980400142568, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.6989700043360189, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 0.9030899869919435, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 1.591064607026499, 0, 0, 0.0, 0.0, 1.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.8450980400142568, 0, 1, 0.0, 0.0, 1.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 1.462397997898956, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.6, 0, 0.0, 1.0, 0.0, 0.0, 0.6020599913279624, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0

[[1.0, 0.0, 0.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.47712125471966244, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 1, 1.0, 0.0, 0.0, 0.0, 0.7781512503836436, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 0.8450980400142568, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.47712125471966244, 0, 1, 0.0, 0.0, 1.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.6, 0, 0.0, 1.0, 0.0, 0.0, 1.041392685158225, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.7781512503836436, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.8, 0, 0.0, 1.0, 0.0, 0.0, 1.041392685158225, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.4, 0, 0.0, 1.0, 0.0, 0.0, 0.9030899869919435, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.6, 0, 0.0, 1.0, 0.0, 0.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0,

[[1.0, 0.0, 0.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.6989700043360189, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.47712125471966244, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.4, 1, 0.0, 1.0, 0.0, 0.0, 1.5185139398778875, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 1, 0.0, 1.0, 0.0, 0.0, 1.6720978579357175, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.9542425094393249, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.7781512503836436, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.6020599913279624, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0

[[1.0, 0.0, 0.0, 0.6, 1, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 1, 0.0, 1.0, 0.0, 0.0, 1.3010299956639813, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.4, 1, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.4, 0, 1.0, 0.0, 0.0, 0.0, 0.3010299956639812, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 0.47712125471966244, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.8, 0, 0.0, 1.0, 0.0, 0.0, 0.0, 1, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.47712125471966244, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 0.6, 0, 0.0, 1.0, 0.0, 0.0, 0.7781512503836436, 0, 0, 1.0, 0.0, 0.0, 1.0, 0.0, 0], [1.0, 0.0, 0.0, 1.0, 0, 0.0, 1.0, 0.0, 0.0, 1.0791812460476249, 0, 0, 1.0, 0.0, 

In [55]:
#todo partitionでぐるぐる回してtransactionRevenueをとってくる
#todo sumdataに合わせてansを当てて設定する。
tmpans=[]
for partitionNumber in range(maxPartition):
    #print(partitionNumber)
    res=getRevenue(forecastStartYmd,forecastEndYmd,partitionNumber,maxPartition)
    for i in range(len(res)):
        #if i==1:
        #    print(res[i])
        tmpans.append([res[i]['key'],res[i]['agg_revenue']['value']])


In [56]:
#集約後のfullVisitorIdにjoinする
#print(tmpans[0])
#ToDo 超遅いので見直す
ans=[]
#npans=np.array(tmpans)
#print(npans[0])
print(sumdata[0][0])

tmpans=sorted(tmpans,key=lambda x:x[0])
print("tmpansソート完了"+str(len(tmpans)) )
print(tmpans[0])

key_ans=tmpans[0][0]
ix_ans=0
key_data=sumdata[0][0]
ix_data=0
inf = '9999999999999999999'

while key_ans != inf or key_data != inf:
    if key_ans == key_data:
        ans.append(tmpans[ix_ans][1])
        ix_data+=1
        ix_ans+=1
    elif key_ans > key_data:
        ans.append(0)
        ix_data+=1
    else:
        ix_ans+=1
    if ix_ans >= len(tmpans):
        key_ans=inf
    else:
        key_ans=tmpans[ix_ans][0]

    if ix_data >= len(sumdata):
        key_data=inf
    else:
        key_data=sumdata[ix_data][0]

#for ix_data in range(len(sumdata)):
#    if ix_data % 10000 ==0:
#        print("join中："+str(ix_data))
    #r = np.where(npans[:,0]==sumdata[i][0])
    
    #print(r[0])
    #print("len:",len(r[0]))
#    if len(r[0])==0:
#        ans.append(0)
#    else:
#        ans.append(r[1]['value'])

    #print(getRevenueByFullVisitorId(rowdata[i][0],"20160101","20180101"))

print(len(ans))
print(sum(ans))

datalength=len(sumdata)

0000010278554503158
tmpansソート完了155959
[u'0000020424342248747', 0.0]
195131
82552430000.0


In [70]:
#tensorflowセットアップ

#print(data[0],ans[0])
#inputData=tf.transpose(data)
debugFlg=False
batch_size=datalength/2
num_elements=18
P=36
num_rows=len(sumdata)
#sumdataから１列目を削除してinputDataに渡す
#data=[]
#for i in range(len(sumdata)):
    #data.append(sumdata[i][1][0])

#print(sumdata[14])
    
data=np.empty((0,num_elements))
for i in range(len(sumdata)):
    #print(sumdata[i][1])
    data=np.append(data,np.array(sumdata[i][1]),axis=0 )

print(data.shape)
print(data[0:3])
#inputData=np.reshape(np.delete(sumdata,0,1),(num_rows,num_elements))
#inputData=np.reshape(sumdata[:][1],(num_rows,num_elements))
##inputData=np.reshape(data,(num_rows,num_elements))
inputData=data,(num_rows,num_elements)
inputAns=np.reshape(ans,(num_rows,1))
x =tf.placeholder("float",[None,num_elements])
y_=tf.placeholder("float",[None,1])

a=tf.Variable( tf.random_uniform([num_elements,1],-1.0,1.0),name="weights")    
w1=tf.Variable( tf.random_uniform([num_elements,P],-1.0,1.0 )  )
w2=tf.Variable( tf.random_uniform([P,1],-1.0,1.0 )  )
#a=tf.Variable( tf.random_uniform([[18]],-1.0,1.0),name="weights")    
#b=tf.Variable(tf.zeros([1,1]),name="intercept")
b=tf.Variable(tf.random_normal([P]),name="intercept")
print("x:",x.shape,"a:",a.shape)
#y=tf.matmul(tf.transpose(a),x)+b
#y=tf.matmul(x,a)
x2=tf.sigmoid(tf.matmul(x,w1))+b
y=tf.matmul(x2,w2)

init = tf.global_variables_initializer()
loss = tf.reduce_sum(tf.square(y_-y))/batch_size
train_step=tf.train.GradientDescentOptimizer(0.01).minimize(loss)


[u'0000679030251760221', array([ 0.3       ,  0.32222222,  0.31111111,  0.31539563])]
[[1.0, 0.0, 0.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 1.041392685158225, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 1, 0.0, 1.0, 0.0, 0.0, 1.0, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.3010299956639812, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.3010299956639812, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[1.0, 0.0, 0.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 1.8808135922807914, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.2, 0, 0.0, 1.0, 0.0, 0.0, 0.3010299956639812, 0, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.2, 1, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0, 0.0, 0]]
[[0.0, 0.0, 1.0, 0.2, 0, 1.0, 0.0, 0.0, 0.0, 0.0, 1, 1, 1.0, 0.0, 0.0, 1.0,

ValueError: all the input arrays must have same number of dimensions

In [ ]:
#データ表示用セットアップ
graphLoss=[]
graphStep=[]
graphNum=20
repeatAll=50000

with tf.Session() as sess:
    sess.run(init)
    print('初期状態')
    inpShape=inputData[0:batch_size]
    ansShape=inputAns[0:batch_size]
    #print('誤差' + str(sess.run(loss, feed_dict={x: inputData[0:batch_size], y_: inputAns[0:batch_size]})))
    ##print('誤差' + str(sess.run(loss, feed_dict={x: inpShape, y_: ansShape})))
    #print("weigths: %f, intercept: %f" % (sess.run(a), sess.run(b) ))
    #print("input:",inputAns[batch_size*step+1:batch_size*step+1+batch_size])
    ##print("weigths:",sess.run(a),"intercept:",sess.run(b) )
    
    for step in range(repeatAll):
        if (batch_size*step) %datalength < (batch_size*step+batch_size) %datalength :
            batchInputData= inputData[(batch_size*step)%datalength:(batch_size*step+batch_size)%datalength]
            batchInputAns = inputAns[(batch_size*step)%datalength:(batch_size*step+batch_size)%datalength]
        else:
            batchInputData= inputData[(batch_size*step)%datalength:min( (batch_size*step+batch_size)%datalength,datalength-1 )]
            batchInputAns = inputAns[(batch_size*step)%datalength:min( (batch_size*step+batch_size)%datalength,datalength-1) ]
        sess.run(train_step, feed_dict={x: batchInputData, y_: batchInputAns })
        if (step+1) % (repeatAll/graphNum) == 0:
            print('\nStep: %s' % (step+1))
            print('誤差' + str(sess.run(loss, feed_dict={x: batchInputData, y_: batchInputAns })))
            if debugFlg==True:
                print("weights:",sess.run(a), " intercept: %f" % ( sess.run(b)))
            graphLoss.append( sess.run(loss, feed_dict={x: batchInputData, y_: batchInputAns }) )
            graphStep.append(step)
    #最終状態を表示
    print("weights1:",sess.run(w1),"weights2:",sess.run(w2), " intercept:", sess.run(b))


In [ ]:
plt.plot(graphStep,graphLoss)